In [ ]:
"""
Combine NALF with Metadynamics attempt
"""

In [2]:
%load_ext autoreload
%autoreload 2
import ObjectiveFunction as of
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
import helper_funcs as hf
from math import sqrt
from scipy.stats import uniform, norm

In [3]:
def cart2polar(x):
    x = np.array(x)
    return np.arctan2(x[1], x[0])

In [9]:
from torch.optim.optimizer import Optimizer, required
import torch
from typing import List, Optional

class SGD_METANALF(Optimizer):

    def __init__(self,
                 params,
                 height: float = required,
                 width: float = required,
                 lr: float = required,
                 alpha:float = required,
                 angle_spread: float = required,
                 levy_spread: float = required,
                 momentum: float = 0
    ):

        if lr is not required and lr < 0.0:
            raise ValueError(f"Invalid learning rate: {lr}")
        if height is not required and height < 0.0:
            raise ValueError(f"Invalid height value: {height}")
        if width is not required and width < 0.0:
            raise ValueError(f"Invalid width value: {width}")
        if momentum < 0.0:
            raise ValueError(f"Invalid momentum value: {momentum}")

        self.height = height
        self.width_denom = -0.5*(1/width)**2
        defaults = dict(height=height,
                        width=width,
                        lr=lr,
                        alpha=alpha,
                        angle_spread=angle_spread,
                        levy_spread=levy_spread,
                        momentum=momentum)
        super().__init__(params, defaults)
    
    def _metric(self, pred):

        if not self.state:
            return pred
        
        history = self.state['history'][0:-1]
        last_ph = self.state['history'][-1]
        
        Vbias = 0

        for ph in history:
            v = last_ph - ph
            Vbias += torch.exp(self.width_denom * torch.dot(v, v.T))
        
        Vbias = self.height * Vbias

        # update detachment of tensors
        self.state['history'][-1] = self.state['history'][-1].detach().clone()
        
        return pred + Vbias


    @torch.no_grad()
    def step(self, closure=None):

        loss = None
        if closure is not None:
            with torch.enable_grad():
                loss = closure() # learn what a closure is 21/04/2022
        
        # Get the current parameter state

        for group in self.param_groups:
            for p in group['params']:
                grad = p.grad
                if 'history' not in self.state:
                    self.state['history'] = [p]
                else:
                    self.state['history'].append(p)

                if 'momentum_buffer' not in self.state:
                    self.state['momentum_buffer'] = grad.detach().clone()
                else:
                    self.state['momentum_buffer'].mul_(group['momentum']).add_(grad, alpha=1)
                grad = self.state['momentum_buffer']
                p.add_(grad, alpha=-group['lr'])

                # NALF
                alpha = group['alpha']
                levy_r = hf.levyrandom(alpha, beta=1, mu=0.0, sigma=group['levy_spread']) * torch.norm(grad)
                cur_dir = cart2polar(grad)
                theta = float(norm.rvs(loc=cur_dir, scale=group['angle_spread']))
                dir = np.array([np.cos(theta), np.sin(theta)])
                levy_noise = levy_r * torch.Tensor(dir)
                p.add_(levy_noise, alpha=-group['lr'])

        return loss

In [5]:
m = of.AlpineN1(start=[2.5, 2], bounds=10)
alpline_NALF = of.OptimisationProblem(
    m,
    SGD_METANALF(m.parameters(),
                lr=0.01, momentum=0.90,
                alpha=1.8, angle_spread=0.15, levy_spread=0.01, 
                height=0.2, width=0.02),
    n_epochs = 1000
)

losses, params, preds = alpline_NALF.run()
fig = alpline_NALF.visualise((-10, 10), (-10, 10), 0.1, render="contour")
fig.show()

Initialised.


In [17]:
m = of.AlpineN1(start=[2.5, 2], bounds=10)
alpline_NALF = of.OptimisationProblem(
    m,
    torch.optim.Adam(m.parameters()),
    n_epochs = 1000
)

losses, params, preds = alpline_NALF.run()
fig = alpline_NALF.visualise((-10, 10), (-10, 10), 0.1, render="contour")
fig.show()

In [15]:
m = of.Ackley(start=[1.0, 1.2], bounds=10)
ackley_METANALF = of.OptimisationProblem(
    m,
    SGD_METANALF(m.parameters(),
                lr=0.01, momentum=0.75,
                alpha=1.8, angle_spread=0.05, levy_spread=0.01, 
                height=0.2, width=0.02),
    n_epochs = 1000
)

losses, params, preds = ackley_METANALF.run()
fig = ackley_METANALF.visualise((-10, 10), (-10, 10), 0.1, render="contour")
fig.show()

In [18]:
"""
Main ideas tried so far:
- SGD with levy flight noise (levy step size, uniform angle dist)
    --> problem: levy step size too large, no convergence guaranteed
    --> need adaptive alpha
- SGD NALF (levy step size, normal angle dist - centered on current gradient direction)
    --> converges better, can customise scale of levy step size dist (its spread) to help control larger step sizes
    --> problem: struggles on flat loss landscapes with many minima
- SGDMeta (metadynamics approach)
    --> explores better, almost always finds the global minimum valley
    --> problem: quadratic time complexity
    --> problem: leaves the valley due to the bias potential
    --> however, spends much of its time in the global minimum valley
    --> theory: metadynamics spends more time in wide, flat valleys - noticed empirically
- SGDMetaCache (finite history cache size)
    --> much faster processing than SGDMeta
    --> no loss of exploration efficiency if cache size is chosen properly
    --> convergence issue is alleviated 
        --> if cache not sufficient or just right (upperbounded), walker stays inside global minimum valley
        --> since it is deep and wide
- SGD META_NALF (combines NALF and META)
    --> ALPINE problem shows that the advantages combine
    --> ACKLEY problem shows that parameter values are very sensitive
    --> therefore need more adaptivity and self-scaling/regularisation
    --> ideas bellow

Main ideas to discuss at next meeting:
Look at uniformity of the angular distribution of actual step direction/gradient direction
- if uniform in some recent window (scaled by cachesize of MD?) --> walker is stuck and oscillating in a valley 
                                                                --> decrease alpha (increase diffusion coefficient)
                                                                --> superdiffusion from NALF
- if non-uniform (tightly distributed) in same window --> walker is converging in a valley or leaving valley
                                                                --> increase alpha (decrease diffusion coefficient)
                                                                --> subdiffusion from NALF
also need to compare current loss against the best loss found so far
- add a gravity term which discourages exploration
- set this proportional to the standard deviation of the current best loss in the sample distribution of losses
- use running mean
- running variance possible?

Idea - Time complexity parameter:
1. start with alpha = 1.0? --> exploration to store local counts (discrete boxes, store counts or metadynamics for continuous)
2. anneal alpha based on local counts + anneal the memory of the walker (shorter history counts)
3. 
"""

"""
Hyperparameter grid search
- batch size 2-1000 (log search lr + linear search alpha) --> parallelise
- 

TMSD
- save 2 datasets : the sum + total number of averages for each lookahead tau
- compute until the average is computed with no less than 50 terms.
"""

'\nHyperparameter grid search\n- batch size 2-1000 (log search)\n'